# TOWARDS A CLEAR UNDERSTANDING OF RURAL INTERNET: WHAT STATISTICAL MEASURES CAN BE USED TO ASSESS, COMPARE AND FORECAST INTERNET SPEEDS FOR RURAL CANADIAN COMMUNITIES?

The Government of Canada has committed to helping 95% of Canadian households and businesses access high-speed internet at minimum speeds of 50 Mbps download and 10 Mbps upload (hereinafter referred to as the “Commitment”) by 2026, and 100% by 2030. According to the CRTC, currently 45.6% of rural community households have access to the Commitment based on what’s available to them via an Internet Service Provider (e.g. Shaw, Telus, etc.) in their region, rather than what a rural household actually realizes at home in terms of internet speeds. 

https://ssc.ca/en/case-study/towards-a-clear-understanding-rural-internet-what-statistical-measures-can-be-used-assess

## Import libraried and read data

In [1]:
import sys
from google.colab import drive
drive.mount('/content/gdrive')
colab_dir = '/content/gdrive/My Drive/Colab_files/2022_CCS_case_study'
sys.path.append(colab_dir)

Mounted at /content/gdrive


In [ ]:
!pip install pmdarima
from pmdarima.arima import auto_arima
from statsmodels.tsa.vector_ar.var_model import VAR

In [3]:
%matplotlib inline
import tqdm
from datetime import datetime
import matplotlib
import matplotlib.pyplot as plt
from datetime import datetime, timedelta
plt.style.use('seaborn')
import pandas as pd
import numpy as np
import warnings
warnings.filterwarnings('ignore')
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from sklearn.metrics import mean_squared_error,r2_score

In [4]:
df = pd.read_csv(colab_dir+'/canada_aggregation_CD_SACTYPE_isrural_conn_type_imputed_step3.csv')
train = pd.read_csv(colab_dir+'/canada_test_imp.csv')
display(train.head(2))
valid = pd.read_csv(colab_dir+'/canada_valid_imp.csv')
display(valid.head(2))
print(train.shape, valid.shape)

date  PRUID  CDUID  SACTYPE  is_rural conn_type  avg_d_mbps_wt  \
0  2019-01-01     10   1001        1     False     fixed     110.345156   
1  2019-01-01     10   1001        1     False    mobile      92.795777   

   avg_u_mbps_wt  avg_lat_ms  tests    DA_POP  imputed  
0      72.589665   10.505591   6618  550285.0    False  
1      28.836200   65.107692    130   43085.0    False

date  PRUID  CDUID  SACTYPE  is_rural conn_type  avg_d_mbps_wt  \
0  2021-10-01     10   1001        1     False     fixed     206.369578   
1  2021-10-01     10   1001        1     False    mobile     140.187612   

   avg_u_mbps_wt  avg_lat_ms  tests    DA_POP  imputed  
0     102.525161   11.942926   9584  640785.0    False  
1      24.954678   38.949468    376  111080.0    False

(30481, 12) (2771, 12)


In [5]:
# “Commitment”: minimum speeds of 50 Mbps download and 10 Mbps upload
df['commitment'] = 0
df.loc[(df.avg_d_mbps_wt>=50) & (df.avg_u_mbps_wt>=10), 'commitment'] = 1 

# Make a prediction for all Census devision

In [6]:
n_models = train.groupby(['PRUID','CDUID','SACTYPE', 'is_rural','conn_type']).size().reset_index().rename(columns={0:'count'})
print(n_models.shape)
print(n_models['count'].value_counts())
n_models.head(2)

(2771, 6)
11    2771
Name: count, dtype: int64


PRUID  CDUID  SACTYPE  is_rural conn_type  count
0     10   1001        1     False     fixed     11
1     10   1001        1     False    mobile     11

## AR Model (using AUTO ARIMA) without covariates

In [22]:
pred = n_models.copy()
pred['avg_d_2026-q1']=0
pred['avg_d_2026-q4']=0
pred['avg_d_2030-q1']=0
pred['avg_d_2030-q4']=0
pred['avg_u_2026-q1']=0
pred['avg_u_2026-q4']=0
pred['avg_u_2030-q1']=0
pred['avg_u_2030-q4']=0
print(pred.shape)

for index, m in tqdm.tqdm(pred.iterrows()):
  colnames = ['CDUID', 'SACTYPE', 'is_rural', 'conn_type']
  m_df = df[df[colnames].eq(m[colnames]).all(axis=1)][['avg_d_mbps_wt', 'avg_u_mbps_wt']]
  #display(m_df)
  y_d =  m_df.iloc[:,0]
  y_u =  m_df.iloc[:,1]

  model_ar = auto_arima(y_d,trace=True, error_action='ignore', start_p=1,start_q=1,max_p=3,max_q=3,
                   suppress_warnings=True,stepwise=False,seasonal=False, verbose = False)
  model_ar.fit(y_d)
  d = model_ar.predict(n_periods=36)
  #print(d)
  model_ar.fit(y_u)
  u = model_ar.predict(n_periods=36)
  pred.iloc[index, 6:] = [d[16], d[19], d[32], d[35], u[16], u[19], u[32], u[35]]
  #break
pred.to_csv(colab_dir+'/pred_ARIMA_2026_2030.csv', index=False)
pred.head(2)

Output hidden; open in https://colab.research.google.com to view.

In [23]:
pred.to_csv(colab_dir+'/pred_ARIMA_2026_2030.csv', index=False)
pred.head(2)

PRUID  CDUID  SACTYPE  is_rural conn_type  count  avg_d_2026-q1  \
0     10   1001        1     False     fixed     11     355.116783   
1     10   1001        1     False    mobile     11     116.822226   

   avg_d_2026-q4  avg_d_2030-q1  avg_d_2030-q4  avg_u_2026-q1  avg_u_2026-q4  \
0     381.341489     494.981918     521.206632     146.980864     154.845523   
1     113.163025      98.585683      95.497702      23.210006      22.905334   

   avg_u_2030-q1  avg_u_2030-q4  
0     188.925711     196.790370  
1      21.630633      21.346693

In [ ]:
pred = pd.read_csv(colab_dir+'/pred_ARIMA_2026_2030.csv')

## ARIMA Model (using AUTOARIMA) without covariates

In [ ]:
pred_arima = n_models.copy()
pred_arima['avg_d_valid']=0
pred_arima['avg_d_pred']=0
pred_arima['avg_u_valid']=0
pred_arima['avg_u_pred']=0

for index, m in tqdm.tqdm(pred_arima.iterrows()):
  colnames = ['CDUID', 'SACTYPE', 'is_rural', 'conn_type']
  m_train = train[train[colnames].eq(m[colnames]).all(axis=1)][['avg_d_mbps_wt', 'avg_u_mbps_wt']]
  m_valid = valid[valid[colnames].eq(m[colnames]).all(axis=1)][['avg_d_mbps_wt', 'avg_u_mbps_wt']]
  
  y_d =  m_train.iloc[:,0]
  y_u =  m_train.iloc[:,1]

  model_ar = auto_arima(y_d,trace=True, error_action='ignore', start_p=1,start_q=1,max_p=3,max_q=3,
                   suppress_warnings=True,stepwise=False,seasonal=False, verbose = False)
  model_ar.fit(y_d)
  d = model_ar.predict(n_periods=1)[0]
  
  model_ar.fit(y_u)
  u = model_ar.predict(n_periods=1)[0]
  pred_arima.iloc[index, 6:10] = [m_valid.iloc[0,0],d,m_valid.iloc[0,1], u]

pred_arima.to_csv(colab_dir+'/pred_ARIMA.csv', index=False)

In [ ]:
pred_arima = pd.read_csv(colab_dir+'/pred_ARIMA.csv')
pred_arima.head(2)

PRUID  CDUID  SACTYPE  is_rural conn_type  count  avg_d_valid  avg_d_pred  \
0     10   1001        1     False     fixed     11   206.369578  219.075558   
1     10   1001        1     False    mobile     11   140.187612  147.105203   

   avg_u_valid  avg_u_pred  
0   102.525161  101.466994  
1    24.954678   25.091812

In [ ]:
RMSE_scores['ARIMA'] = [np.sqrt(mean_squared_error(pred_arima["avg_d_valid"],pred_arima['avg_d_pred'])),
                     np.sqrt(mean_squared_error(pred_arima["avg_u_valid"],pred_arima['avg_u_pred']))]


print("Root Mean Square Error for ARIMA Model for download speed: ",np.sqrt(mean_squared_error(pred_arima["avg_d_valid"],pred_arima['avg_d_pred'])))
print("Root Mean Square Error for  Model for upload speed: ",np.sqrt(mean_squared_error(pred_arima["avg_u_valid"],pred_arima['avg_u_pred'])))

print("Mean Square Error for ARIMA Model for download speed: ",mean_squared_error(pred_arima["avg_d_valid"],pred_arima['avg_d_pred']))
print("Mean Square Error for ARIMA Model for upload speed: ",mean_squared_error(pred_arima["avg_u_valid"],pred_arima['avg_u_pred']))

Root Mean Square Error for ARIMA Model for download speed:  44.35681342800491
Root Mean Square Error for  Model for upload speed:  19.748978518708693
Mean Square Error for ARIMA Model for download speed:  1967.5268974868368
Mean Square Error for ARIMA Model for upload speed:  390.02215253241735


## stepwise ARIMA Model without covariates

In [ ]:
pred_arima_sw = n_models.copy()
pred_arima_sw['avg_d_valid']=0
pred_arima_sw['avg_d_pred']=0
pred_arima_sw['avg_u_valid']=0
pred_arima_sw['avg_u_pred']=0

for index, m in tqdm.tqdm(pred_arima_sw.iterrows()):
  colnames = ['CDUID', 'SACTYPE', 'is_rural', 'conn_type']
  m_train = train[train[colnames].eq(m[colnames]).all(axis=1)][['avg_d_mbps_wt', 'avg_u_mbps_wt']]
  m_valid = valid[valid[colnames].eq(m[colnames]).all(axis=1)][['avg_d_mbps_wt', 'avg_u_mbps_wt']]
  
  y_d =  m_train.iloc[:,0]
  y_u =  m_train.iloc[:,1]
  display(y_d)
  model_ar = auto_arima(y_d,trace=True, error_action='ignore', start_p=1,start_q=1,max_p=3,max_q=3,m=2,
                   suppress_warnings=True,stepwise=False,seasonal=True, verbose = False)
  model_ar.fit(y_d)
  d = model_ar.predict(n_periods=1)[0]
  
  model_ar.fit(y_u)
  u = model_ar.predict(n_periods=1)[0]
  pred_arima_sw.iloc[index, 6:10] = [m_valid.iloc[0,0],d,m_valid.iloc[0,1], u]

pred_arima_sw.to_csv(colab_dir+'/pred_ARIMA_sw.csv', index=False)

0it [00:00, ?it/s]

0        110.345156
2765     119.111294
5531     119.289840
8297     133.982140
11063    138.116998
13832    140.703344
16597    153.448422
19360    173.906028
22130    173.031194
24901    205.127325
27672    198.021289
Name: avg_d_mbps_wt, dtype: float64

 ARIMA(0,0,0)(0,1,0)[2] intercept   : AIC=68.317, Time=0.02 sec
 ARIMA(0,0,0)(0,1,1)[2] intercept   : AIC=70.141, Time=0.12 sec
 ARIMA(0,0,0)(0,1,2)[2] intercept   : AIC=inf, Time=0.22 sec
 ARIMA(0,0,0)(1,1,0)[2] intercept   : AIC=70.241, Time=0.11 sec
 ARIMA(0,0,0)(1,1,1)[2] intercept   : AIC=inf, Time=0.49 sec
 ARIMA(0,0,0)(1,1,2)[2] intercept   : AIC=inf, Time=0.52 sec
 ARIMA(0,0,0)(2,1,0)[2] intercept   : AIC=70.194, Time=0.30 sec
 ARIMA(0,0,0)(2,1,1)[2] intercept   : AIC=inf, Time=0.36 sec
 ARIMA(0,0,0)(2,1,2)[2] intercept   : AIC=inf, Time=0.50 sec
 ARIMA(0,0,1)(0,1,0)[2] intercept   : AIC=69.990, Time=0.09 sec
 ARIMA(0,0,1)(0,1,1)[2] intercept   : AIC=71.934, Time=0.14 sec
 ARIMA(0,0,1)(0,1,2)[2] intercept   : AIC=inf, Time=0.43 sec
 ARIMA(0,0,1)(1,1,0)[2] intercept   : AIC=71.964, Time=0.17 sec
 ARIMA(0,0,1)(1,1,1)[2] intercept   : AIC=inf, Time=0.51 sec
 ARIMA(0,0,1)(1,1,2)[2] intercept   : AIC=inf, Time=0.39 sec
 ARIMA(0,0,1)(2,1,0)[2] intercept   : AIC=72.116, Time=0.40 sec


1it [00:12, 12.31s/it]

 ARIMA(1,0,1)(2,1,1)[2] intercept   : AIC=inf, Time=0.28 sec

Best model:  ARIMA(0,0,0)(0,1,0)[2] intercept
Total fit time: 12.244 seconds


...

2505     22.417423
5270     26.135039
8036     37.013125
10802    47.008488
13568    26.402974
16337    38.623226
19102    31.406397
21865    42.659735
24635    51.615490
27406    35.614846
30177    32.176617
Name: avg_d_mbps_wt, dtype: float64

 ARIMA(0,0,0)(0,1,0)[2] intercept   : AIC=76.539, Time=0.01 sec
 ARIMA(0,0,0)(0,1,1)[2] intercept   : AIC=inf, Time=0.15 sec
 ARIMA(0,0,0)(0,1,2)[2] intercept   : AIC=inf, Time=0.30 sec
 ARIMA(0,0,0)(1,1,0)[2] intercept   : AIC=74.228, Time=0.09 sec
 ARIMA(0,0,0)(1,1,1)[2] intercept   : AIC=inf, Time=0.31 sec
 ARIMA(0,0,0)(1,1,2)[2] intercept   : AIC=inf, Time=0.43 sec
 ARIMA(0,0,0)(2,1,0)[2] intercept   : AIC=73.836, Time=0.05 sec
 ARIMA(0,0,0)(2,1,1)[2] intercept   : AIC=inf, Time=0.27 sec
 ARIMA(0,0,0)(2,1,2)[2] intercept   : AIC=inf, Time=0.54 sec
 ARIMA(0,0,1)(0,1,0)[2] intercept   : AIC=77.821, Time=0.03 sec
 ARIMA(0,0,1)(0,1,1)[2] intercept   : AIC=inf, Time=0.11 sec
 ARIMA(0,0,1)(0,1,2)[2] intercept   : AIC=inf, Time=0.33 sec
 ARIMA(0,0,1)(1,1,0)[2] intercept   : AIC=inf, Time=0.13 sec
 ARIMA(0,0,1)(1,1,1)[2] intercept   : AIC=inf, Time=0.35 sec
 ARIMA(0,0,1)(1,1,2)[2] intercept   : AIC=inf, Time=0.46 sec
 ARIMA(0,0,1)(2,1,0)[2] intercept   : AIC=inf, Time=0.30 sec
 ARIMA(0,0,1

2506it [5:39:40, 10.00s/it]

2506      10.446594
5271       4.670089
8037       4.011515
10803      6.327357
13569      5.838000
16338      7.169682
19103      5.093355
21866     11.056444
24636     10.694892
27407    140.054317
30178     34.744552
Name: avg_d_mbps_wt, dtype: float64

 ARIMA(0,0,0)(0,1,0)[2] intercept   : AIC=95.991, Time=0.02 sec
 ARIMA(0,0,0)(0,1,1)[2] intercept   : AIC=97.968, Time=0.08 sec
 ARIMA(0,0,0)(0,1,2)[2] intercept   : AIC=99.781, Time=0.15 sec
 ARIMA(0,0,0)(1,1,0)[2] intercept   : AIC=97.984, Time=0.08 sec
 ARIMA(0,0,0)(1,1,1)[2] intercept   : AIC=inf, Time=0.31 sec
 ARIMA(0,0,0)(1,1,2)[2] intercept   : AIC=inf, Time=0.46 sec
 ARIMA(0,0,0)(2,1,0)[2] intercept   : AIC=99.868, Time=0.06 sec
 ARIMA(0,0,0)(2,1,1)[2] intercept   : AIC=inf, Time=0.35 sec
 ARIMA(0,0,0)(2,1,2)[2] intercept   : AIC=inf, Time=0.46 sec
 ARIMA(0,0,1)(0,1,0)[2] intercept   : AIC=97.950, Time=0.03 sec
 ARIMA(0,0,1)(0,1,1)[2] intercept   : AIC=99.941, Time=0.09 sec
 ARIMA(0,0,1)(0,1,2)[2] intercept   : AIC=101.781, Time=0.22 sec
 ARIMA(0,0,1)(1,1,0)[2] intercept   : AIC=99.946, Time=0.16 sec
 ARIMA(0,0,1)(1,1,1)[2] intercept   : AIC=101.946, Time=0.20 sec
 ARIMA(0,0,1)(1,1,2)[2] intercept   : AIC=inf, Time=0.45 sec
 ARIMA(0,0,1)(2,1,0)[2] intercept   : AIC=101.854, Ti

In [ ]:
mse_d = mean_squared_error(pred_arima_sw["avg_d_valid"],pred_arima_sw['avg_d_pred'])
mse_u = mean_squared_error(pred_arima_sw["avg_u_valid"],pred_arima_sw['avg_u_pred'])
RMSE_scores['ARIMA'] = [np.sqrt(mse_d), np.sqrt(mse_u)]

print("Root Mean Square Error for ARIMA Model for download speed: ",np.sqrt(mse_d))
print("Root Mean Square Error for  Model for upload speed: ",np.sqrt(mse_u))

print("Mean Square Error for ARIMA Model for download speed: ",mse_d)
print("Mean Square Error for ARIMA Model for upload speed: ",mse_u)

## AR Model with exogenous variables

In [ ]:
#exogenous_var = ['CDUID','DA_POP', 'SACTYPE', 'conn_fixed']
exogenous_var = ['DA_POP', 'SACTYPE', 'conn_fixed']
model_ar_e= auto_arima(train["pc1"],trace=True, error_action='ignore', start_p=0,start_q=0,max_p=4,max_q=0,
                   suppress_warnings=True,stepwise=False,seasonal=False,
                   exogeneous=train[exogenous_var], stationarity=False, seasonality=True)
model_ar_e.fit(train["pc1"], exogenous=train[exogenous_var])

 ARIMA(0,1,0)(0,0,0)[0] intercept   : AIC=220834.212, Time=0.86 sec
 ARIMA(1,1,0)(0,0,0)[0] intercept   : AIC=214975.369, Time=1.83 sec
 ARIMA(2,1,0)(0,0,0)[0] intercept   : AIC=213342.143, Time=2.79 sec
 ARIMA(3,1,0)(0,0,0)[0] intercept   : AIC=211686.988, Time=3.61 sec
 ARIMA(4,1,0)(0,0,0)[0] intercept   : AIC=211035.012, Time=2.89 sec

Best model:  ARIMA(4,1,0)(0,0,0)[0] intercept
Total fit time: 12.007 seconds


ARIMA(order=(4, 1, 0), scoring_args={}, suppress_warnings=True)

In [ ]:
prediction_ar_e=model_ar_e.predict(len(valid), exogenous=valid[exogenous_var])
y_pred["AR Model Prediction with exogenous variables"]=prediction_ar_e

In [ ]:
RMSE_scores.append(np.sqrt(mean_squared_error(y_pred["pc1"],prediction_ar_e)))
MSE_scores.append(mean_squared_error(y_pred["pc1"],prediction_ar_e))
print("Root Mean Square Error for AR Model Prediction with exogenous variables: ",np.sqrt(mean_squared_error(y_pred["pc1"],prediction_ar_e)))
print("Mean Square Error for AR Model Prediction with exogenous variables: ",mean_squared_error(y_pred["pc1"],prediction_ar_e))

Root Mean Square Error for AR Model Prediction with exogenous variables:  57.528334090581396
Mean Square Error for AR Model Prediction with exogenous variables:  3309.5092232375496


## Model comparison

In [ ]:
model_names=["Auto Regressive Model (AR)","ARIMA Model","Auto Regressive Model with exogenous variables", 
             "Recursive autoregressive model", "Recursive autoregressive model with exogenous variables"]
model_summary=pd.DataFrame(RMSE_scores, columns=["Model Name","RMSE download", "RMSE upload"]).sort_values(["Root Mean Squared Error"])
model_summary

NameError: ignored

In [ ]:
RMSE_scores